# Segment provinces


Create wijk and gemeente level segmentations for two Dutch provinces, Groningen and Friesland, and save as geojson and Gabmap KML.

All is based on [CBS data](https://www.cbs.nl/nl-nl/dossier/nederland-regionaal/geografische%20data/wijk-en-buurtkaart-2017)

For Friesland, several wijken are merged, in particular those of the municipalities Ameland, Harlingen, Schiermonnikoog, Terschelling and Vlieland, and those of Leeuwarden with centroid above 53.167. These neighborhoods are small in area and hence we decided to merge, to avoid a 

In [1]:
%load_ext autoreload

%autoreload 2

In [2]:
import sys
sys.path.append('../')

from stimmen.latitude_longitude import reverse_latitude_longitude
from stimmen.shapefile import shapefiles_to_geojson
from stimmen.cbs import gwb_in_province, get_available_provinces
from stimmen.geojson import merge_features
from gabmap import as_gabmap_kml

from shapely.geometry import shape, box, mapping

import json
import folium
import pickle

from collections import defaultdict

In [4]:
for province in ['Groningen', 'Friesland']:
    wijken_geojson = gwb_in_province(province, 'wijk', 2018, polygon_simplification=None)
    gemeente_geojson = gwb_in_province(province, 'gem', 2018, polygon_simplification=None)
    
    if province == 'Friesland':
        for gemeente in {'Ameland', 'Harlingen', 'Schiermonnikoog', 'Terschelling', 'Vlieland'}:
            merged_geojson = merge_features(
                wijken_geojson.copy(),
                condition=lambda feature: feature['properties']['GM_NAAM'] == gemeente,
                aggregate={'WK_NAAM': ' '.join}
            )

        merge_leeuwarden_only_above_latitude = 53.167
        wijken_geojson = merge_features(
            wijken_geojson,
            condition=lambda feature: (
                feature['properties']['GM_NAAM'] == 'Leeuwarden' and
                shape(feature['geometry']).centroid.y > merge_leeuwarden_only_above_latitude
            ),
            aggregate={'WK_NAAM': ' '.join}
        )
    
    #Some gemeentes appear twice in the cbs data.
    for gemeente in [feature['properties']['GM_NAAM'] for feature in gemeente_geojson['features']]:
        gemeente_geojson = merge_features(
            gemeente_geojson, condition=lambda feature: feature['properties']['GM_NAAM'] == gemeente)
    
    for feature in wijken_geojson['features']:
        feature['properties']['gemeente_en_wijk_naam'] = (
            feature['properties']['GM_NAAM'] +
            ', ' +
            feature['properties'].get('WK_NAAM', '')
        ).replace('&', 'en').replace('/', ' ').replace('"', ' ').replace("'", ' ')
    
    for feature in gemeente_geojson['features']:
        feature['properties']['gemeente_naam'] = (
            feature['properties']['GM_NAAM']
        ).replace('&', 'en').replace('/', ' ').replace('"', ' ').replace("'", ' ')
    
    with open('../data/{}_wijken.geojson'.format(province), 'w') as f:
        json.dump(wijken_geojson, f)
    with open('../data/{}_gemeentes.geojson'.format(province), 'w') as f:
        json.dump(gemeente_geojson, f)
    
    with open('../data/{}_wijken.kml'.format(province), 'w') as f:
        f.write(as_gabmap_kml(wijken_geojson, name_property='gemeente_en_wijk_naam'))
    with open('../data/{}_gemeentes.kml'.format(province), 'w') as f:
        f.write(as_gabmap_kml(gemeente_geojson, name_property='gemeente_naam'))

Groningen
0
1
2
3
4
5
6
Friesland
0
1
2
3
4
5
6
